In [1]:
from __future__ import unicode_literals, print_function, division
from io import open
import unicodedata
import re
import random

import nltk
from nltk.tokenize import word_tokenize

import time
import datetime

import torch
import torch.nn as nn
from torch import optim
import torch.nn.functional as F

import numpy as np
from torch.utils.data import TensorDataset, DataLoader, RandomSampler, Dataset

import json
import pandas as pd

In [2]:
random.seed(21)
torch.manual_seed(21)
np.random.seed(21)

In [3]:
dataset_pandas = pd.read_csv("expand_natural_texts_0004.res.tsv", sep='\t', header=None)

In [4]:
dataset_pandas = dataset_pandas.sample(frac = 1)
msk = np.random.rand(len(dataset_pandas)) < 0.9
dataset_pandas_test = dataset_pandas[~msk]
dataset_pandas_tmp = dataset_pandas[msk]

msk = np.random.rand(len(dataset_pandas_tmp)) < 0.9
dataset_pandas_validate = dataset_pandas_tmp[~msk]
dataset_pandas_train = dataset_pandas_tmp[msk]

In [5]:
nltk.download('punkt_tab')

[nltk_data] Downloading package punkt_tab to
[nltk_data]     /home/xmikusek/nltk_data...
[nltk_data]   Package punkt_tab is already up-to-date!


True

In [6]:
device = torch.device("cuda" if torch.cuda.is_available() else "cpu")
device.type

'cuda'

In [7]:
SOS_token = 0
EOS_token = 1
EMP_token = 2

In [8]:
class DatasetNatural2CQL(Dataset):
    def __init__(self):
        self.data_unprocessed = []
        self.natual_text = []
        self.word2id = {".SOS.": SOS_token, ".EOS.": EOS_token, ".EMP.": EMP_token}
        self.cql2id = {".SOS.": SOS_token, ".EOS.": EOS_token, ".EMP.": EMP_token}
        self.texts = []
        self.cqls = []

    def load_pandas(self, dataset):
        for line in dataset.iloc:
            texts_json = json.loads(line[4])
            texts_extracted = texts_json["data"][0]["content"][0]["text"]["value"].split("\n")
            texts_tokenized, cql_tokenized = self.make_transaltion(texts_extracted, line[2])
            self.add_transaltions_tokenized(texts_tokenized, cql_tokenized)

    def load_tsv(self, path):
        with open(path, "r") as file_data:
            for line in file_data:
                line = line.strip()
                line = line.split("\t")
                texts_json = json.loads(line[4])
                texts_extracted = texts_json["data"][0]["content"][0]["text"]["value"].split("\n")
                texts_tokenized, cql_tokenized = self.make_transaltion(texts_extracted, line[2])
                self.add_transaltions_tokenized(texts_tokenized, cql_tokenized)

    def process_text(self, text):
        self.is_in_quote = False
        def make_triplet(token):
            for i in range(len(token) // 3):
                yield token[i*3:i*3+3]
            if len(token) % 3 != 0:
                yield token[(len(token) // 3)*3:]
        def resolve_quotes(tokens):
            for token in tokens:
                if token == '``':
                    self.is_in_quote = True
                    yield token
                    continue
                if token == "''":
                    self.is_in_quote = False
                    yield token
                    continue
                if self.is_in_quote:
                    for c in token:
                        yield c
                else:
                    yield token
        triplets = []
        for word_token in resolve_quotes(word_tokenize(text)):
            triplets = triplets + list(make_triplet(word_token))
        return triplets

    def process_cql(self, cql):
        return cql.strip()

    def make_transaltion(self, texts, cql):
        cql_tokenized = self.process_cql(cql)
        texts_tokenized = []
        for text in texts:
            texts_tokenized.append(self.process_text(text))
        return texts_tokenized, cql_tokenized

    def add_transaltions_tokenized(self, texts, cql):
        for text in texts:
            for t in text:
                if t not in self.word2id:
                    self.word2id[t] = len(self.word2id)
        for t in cql:
            if t not in self.cql2id:
                self.cql2id[t] = len(self.cql2id)
        cql_numeric = []
        for t in cql:
            cql_numeric.append(self.cql2id[t])

        texts_numeric = []
        for text in texts:
            text_numeric = []
            for t in text:
                text_numeric.append(self.word2id[t])
            if len(text_numeric) == 0 or len(cql_numeric) == 0:
                continue
            texts_numeric.append(text_numeric)
        if len(texts_numeric) == 0:
            return
        self.data_unprocessed.append((texts_numeric, cql_numeric))
                
    def finalize(self, device):
        self.id2cql = {}
        self.NUMER_OF_RECORDS = 0
        self.MAXIMAL_LENGTH = -1
        for texts, cql in self.data_unprocessed:
            if self.MAXIMAL_LENGTH < len(cql):
                self.MAXIMAL_LENGTH = len(cql)
            self.NUMER_OF_RECORDS += len(texts)
            for text in texts:
                if self.MAXIMAL_LENGTH < len(text):
                    self.MAXIMAL_LENGTH = len(text)

        in_values = np.zeros((self.NUMER_OF_RECORDS, self.MAXIMAL_LENGTH+1), dtype=np.int32)
        out_values = np.zeros((self.NUMER_OF_RECORDS, self.MAXIMAL_LENGTH+1), dtype=np.int32)

        i = 0
        for texts, cql in self.data_unprocessed:
            for text in texts:
                in_values[i, :len(text)] = text
                out_values[i, :len(cql)] = cql
                in_values[i, len(text)] = EOS_token
                out_values[i, len(cql)] = EOS_token
                i += 1

        self.inputs = torch.LongTensor(in_values).to(device)
        self.outputs = torch.LongTensor(out_values).to(device)

        for val in self.cql2id:
            self.id2cql[self.cql2id[val]] = val

    def prepare_for_eval(self, dataset):
        max_len = dataset.MAXIMAL_LENGTH

        self.inputs = self.inputs.to("cpu")
        self.outputs = self.outputs.to("cpu")
        in_values = self.inputs.numpy()
        out_values = self.outputs.numpy()

        in_values_new = np.zeros((self.NUMER_OF_RECORDS, max_len+1), dtype=np.int32)
        out_values_new = np.zeros((self.NUMER_OF_RECORDS, max_len+1), dtype=np.int32)

        if max_len > self.MAXIMAL_LENGTH:
            for i in range(self.NUMER_OF_RECORDS):
                for j in range(self.MAXIMAL_LENGTH+1):
                    val = in_values[i][j]
                    if val >= len(dataset.word2id):
                        val = EMP_token
                    in_values_new[i][j] = val
                    out_values_new[i][j] = out_values[i][j]

        else:
            for i in range(self.NUMER_OF_RECORDS):
                for j in range(max_len):
                    val = in_values[i][j]
                    if val >= len(dataset.word2id):
                        val = EMP_token
                    in_values_new[i][j] = val
                    out_values_new[i][j] = out_values[i][j]
                in_values_new[i][max_len] = EMP_token
                out_values_new[i][max_len] = EMP_token

        self.inputs = torch.LongTensor(in_values_new).to(device)
        self.outputs = torch.LongTensor(out_values_new).to(device)
            

    def __len__(self):
        return self.NUMER_OF_RECORDS

    def __getitem__(self, idx):
        if idx < self.NUMER_OF_RECORDS:
            return self.inputs[idx], self.outputs[idx]
        idx = idx % len(self.texts)
        text_tensor = self.inputs[idx].clone()
        text_tensor[random.randint(0, len(self.inputs[idx]) - 1)] = EMP_token
        return text_tensor, self.cqls[idx]

In [9]:
dataset_natural2cql_train = DatasetNatural2CQL()
dataset_natural2cql_train.load_pandas(dataset_pandas_train)
dataset_natural2cql_train.finalize(device)

In [10]:
dataset_natural2cql_validation = DatasetNatural2CQL()
dataset_natural2cql_validation.word2id = dataset_natural2cql_train.word2id.copy()
dataset_natural2cql_validation.cql2id = dataset_natural2cql_train.cql2id.copy()
dataset_natural2cql_validation.load_pandas(dataset_pandas_validate)
dataset_natural2cql_validation.finalize(device)
dataset_natural2cql_validation.prepare_for_eval(dataset_natural2cql_train)

In [11]:
dataset_natural2cql_test = DatasetNatural2CQL()
dataset_natural2cql_test.word2id = dataset_natural2cql_train.word2id.copy()
dataset_natural2cql_test.cql2id = dataset_natural2cql_train.cql2id.copy()
dataset_natural2cql_test.load_pandas(dataset_pandas_test)
dataset_natural2cql_test.finalize(device)
dataset_natural2cql_test.prepare_for_eval(dataset_natural2cql_train)

In [12]:
def save_model(encoder, decoder, dataset, prefix=""):
    torch.save(encoder.state_dict(), prefix + "encoder.pt")
    torch.save(decoder.state_dict(), prefix + "decoder.pt")
    with open(prefix + "metadata.txt", "w") as f:
        f.write(f"{dataset.MAXIMAL_LENGTH}\n")
        f.write(f"{json.dumps(dataset.word2id)}\n")
        f.write(f"{json.dumps(dataset.id2cql)}\n")

In [13]:
class EncoderRNN(nn.Module):
    def __init__(self, input_size, hidden_size, dropout_p=0.1):
        super(EncoderRNN, self).__init__()
        self.hidden_size = hidden_size

        self.embedding = nn.Embedding(input_size, hidden_size)
        self.gru = nn.GRU(hidden_size, hidden_size, batch_first=True)
        self.dropout = nn.Dropout(dropout_p)

    def forward(self, input):
        embedded = self.dropout(self.embedding(input))
        output, hidden = self.gru(embedded)
        return output, hidden

In [14]:
class DecoderRNN(nn.Module):
    def __init__(self, hidden_size, output_size):
        super(DecoderRNN, self).__init__()
        self.embedding = nn.Embedding(output_size, hidden_size)
        self.gru = nn.GRU(hidden_size, hidden_size, batch_first=True)
        self.out = nn.Linear(hidden_size, output_size)

    def forward(self, encoder_outputs, encoder_hidden, target_tensor=None):
        batch_size = encoder_outputs.size(0)
        decoder_input = torch.empty(batch_size, 1, dtype=torch.long, device=device).fill_(SOS_token)
        decoder_hidden = encoder_hidden
        decoder_outputs = []

        for i in range(MAX_LENGTH):
            decoder_output, decoder_hidden  = self.forward_step(decoder_input, decoder_hidden)
            decoder_outputs.append(decoder_output)

            if target_tensor is not None:
                # Teacher forcing: Feed the target as the next input
                decoder_input = target_tensor[:, i].unsqueeze(1) # Teacher forcing
            else:
                # Without teacher forcing: use its own predictions as the next input
                _, topi = decoder_output.topk(1)
                decoder_input = topi.squeeze(-1).detach()  # detach from history as input

        decoder_outputs = torch.cat(decoder_outputs, dim=1)
        decoder_outputs = F.log_softmax(decoder_outputs, dim=-1)
        return decoder_outputs, decoder_hidden, None # We return `None` for consistency in the training loop

    def forward_step(self, input, hidden):
        output = self.embedding(input)
        output = F.relu(output)
        output, hidden = self.gru(output, hidden)
        output = self.out(output)
        return output, hidden


In [15]:
class BahdanauAttention(nn.Module):
    def __init__(self, hidden_size):
        super(BahdanauAttention, self).__init__()
        self.Wa = nn.Linear(hidden_size, hidden_size)
        self.Ua = nn.Linear(hidden_size, hidden_size)
        self.Va = nn.Linear(hidden_size, 1)

    def forward(self, query, keys):
        scores = self.Va(torch.tanh(self.Wa(query) + self.Ua(keys)))
        scores = scores.squeeze(2).unsqueeze(1)

        weights = F.softmax(scores, dim=-1)
        context = torch.bmm(weights, keys)

        return context, weights

class AttnDecoderRNN(nn.Module):
    def __init__(self, hidden_size, output_size, max_length, dropout_p=0.1):
        super(AttnDecoderRNN, self).__init__()
        self.embedding = nn.Embedding(output_size, hidden_size)
        self.attention = BahdanauAttention(hidden_size)
        self.gru = nn.GRU(2 * hidden_size, hidden_size, batch_first=True)
        self.out = nn.Linear(hidden_size, output_size)
        self.dropout = nn.Dropout(dropout_p)
        self.max_length = max_length

    def forward(self, encoder_outputs, encoder_hidden, target_tensor=None):
        batch_size = encoder_outputs.size(0)
        decoder_input = torch.empty(batch_size, 1, dtype=torch.long, device=device).fill_(SOS_token)
        decoder_hidden = encoder_hidden
        decoder_outputs = []
        attentions = []

        for i in range(self.max_length):
            decoder_output, decoder_hidden, attn_weights = self.forward_step(
                decoder_input, decoder_hidden, encoder_outputs
            )
            decoder_outputs.append(decoder_output)
            attentions.append(attn_weights)

            if target_tensor is not None:
                # Teacher forcing: Feed the target as the next input
                decoder_input = target_tensor[:, i].unsqueeze(1) # Teacher forcing
            else:
                # Without teacher forcing: use its own predictions as the next input
                _, topi = decoder_output.topk(1)
                decoder_input = topi.squeeze(-1).detach()  # detach from history as input

        decoder_outputs = torch.cat(decoder_outputs, dim=1)
        decoder_outputs = F.log_softmax(decoder_outputs, dim=-1)
        attentions = torch.cat(attentions, dim=1)

        return decoder_outputs, decoder_hidden, attentions


    def forward_step(self, input, hidden, encoder_outputs):
        embedded =  self.dropout(self.embedding(input))

        query = hidden.permute(1, 0, 2)
        context, attn_weights = self.attention(query, encoder_outputs)
        input_gru = torch.cat((embedded, context), dim=2)

        output, hidden = self.gru(input_gru, hidden)
        output = self.out(output)

        return output, hidden, attn_weights

In [16]:
def evalueate(dataset, encoder, decoder, cql2id):
    space_token = cql2id[" "]
    encoder.train(False)
    decoder.train(False)

    # exact match
    exact_match = 0
    tested_match = 0
    for data in DataLoader(dataset, batch_size=64, shuffle=False):
        input_tensor, target_tensor = data
        with torch.no_grad():
            encoder_outputs, encoder_hidden = encoder(input_tensor)
            decoder_outputs, decoder_hidden, decoder_attn = decoder(encoder_outputs, encoder_hidden)
        _, topi = decoder_outputs.topk(1)
        decoded_ids = topi.squeeze()
        target_tensor = target_tensor.to("cpu")
        decoded_ids = decoded_ids.to("cpu")
        target_list = target_tensor.tolist()
        decoded_list = decoded_ids.tolist()
        for val in range(len(decoded_list)):
            EOS_pos = 0
            while EOS_pos < len(decoded_list[val]) and decoded_list[val][EOS_pos] != EOS_token:
                EOS_pos += 1
            decoded_list[val] = decoded_list[val][:EOS_pos]

            EOS_pos = 0
            while EOS_pos < len(target_list[val]) and target_list[val][EOS_pos] != EOS_token:
                EOS_pos += 1
            target_list[val] = target_list[val][:EOS_pos]
            
            while True:
                try:
                    decoded_list[val].remove(space_token)
                except ValueError:
                    break
            while True:
                try:
                    target_list[val].remove(space_token)
                except ValueError:
                    break
            if decoded_list[val] == target_list[val]:
                exact_match += 1
            tested_match += 1
    return exact_match, tested_match

In [17]:
def train_epoch(dataloader, encoder, decoder, encoder_optimizer, decoder_optimizer, criterion, logger_file=None):
    total_loss = 0
    iterations = 0
    start_time = time.time()
    for data in dataloader:
        if iterations % 100 == 0:
            print(f"Iteration: {iterations}/{len(dataloader)}")
        input_tensor, target_tensor = data
        iterations += 1

        encoder_optimizer.zero_grad()
        decoder_optimizer.zero_grad()

        encoder_outputs, encoder_hidden = encoder(input_tensor)
        decoder_outputs, _, _ = decoder(encoder_outputs, encoder_hidden, target_tensor)

        loss = criterion(
            decoder_outputs.view(-1, decoder_outputs.size(-1)),
            target_tensor.view(-1)
        )
        loss.backward()

        encoder_optimizer.step()
        decoder_optimizer.step()

        total_loss += loss.item()
    end_time = time.time()
    print(f"[{datetime.datetime.now().isoformat()}] Epoch took: {int(end_time - start_time)} seconds.")
    save_model(encoder, decoder, dataset_natural2cql_train, "autosave_")
    
    exact_match, num_of_match = evalueate(dataset_natural2cql_validation, encoder, decoder, dataset_natural2cql_train.cql2id)
    encoder.train(True)
    decoder.train(True)

    print(f"[{datetime.datetime.now().isoformat()}] Match: {exact_match / num_of_match} ({exact_match} / {num_of_match})\n")
    
    if logger_file is not None:
        logger_file.write(f"[{datetime.datetime.now().isoformat()}] Epoch took: {int(end_time - start_time)} seconds.\n")
        logger_file.write(f"[{datetime.datetime.now().isoformat()}] Loss: {total_loss / len(dataloader)}\n")
        logger_file.write(f"[{datetime.datetime.now().isoformat()}] Match: {exact_match / num_of_match} ({exact_match} / {num_of_match})\n")
        logger_file.flush()
    return total_loss / len(dataloader)

In [18]:
def train(train_dataloader, encoder, decoder, n_epochs, learning_rate=0.001):
        encoder.train(True)
        decoder.train(True)
        logger_file = open("log_fix.txt", "a")
        encoder_optimizer = optim.Adam(encoder.parameters(), lr=learning_rate)
        decoder_optimizer = optim.Adam(decoder.parameters(), lr=learning_rate)
        criterion = nn.NLLLoss()
        for epoch in range(1, n_epochs + 1):
            loss = train_epoch(train_dataloader, encoder, decoder, encoder_optimizer, decoder_optimizer, criterion, logger_file=logger_file)
            print(f"[{datetime.datetime.now().isoformat()}] Loss: {loss}")
        logger_file.close()

In [19]:
hidden_size = 128

encoder = EncoderRNN(len(dataset_natural2cql_train.word2id), hidden_size).to(device)
decoder = AttnDecoderRNN(hidden_size, len(dataset_natural2cql_train.cql2id), dataset_natural2cql_train.MAXIMAL_LENGTH+1).to(device)

In [ ]:
train_dataloader = DataLoader(dataset_natural2cql_train, batch_size=64, shuffle=True)
train(train_dataloader, encoder, decoder, 600)

Iteration: 0/1328


In [ ]:
def make_input(sentence, max_length, word2id):
    sent = word_tokenize(sentence)
    values = []
    for t in sent:
        try:
            values.append(word2id[t])
        except Exception:
            values.append(EMP_token)
    res = np.zeros(max_length+1, np.int32)
    res[:len(values)] = values
    res[len(values)] = EOS_token
    return np.array([res])

In [ ]:
def make_output(sentence, cql2id):
    response = []
    for t in sentence:
        if t == EOS_token:
            break
        response.append(cql2id[int(t)])
    return "".join(response)

In [ ]:
val = make_input("All lemmas cat followed by any verb or any noun.", dataset_natural2cql_train.MAXIMAL_LENGTH, dataset_natural2cql_train.word2id)

In [ ]:
with torch.no_grad():
    encoder_outputs, encoder_hidden = encoder(torch.LongTensor(val).to(device))
    decoder_outputs, decoder_hidden, decoder_attn = decoder(encoder_outputs, encoder_hidden)

In [ ]:
_, topi = decoder_outputs.topk(1)
decoded_ids = topi.squeeze()

In [ ]:
decoded_ids = decoded_ids.to("cpu")

In [ ]:
make_output(decoded_ids, dataset_natural2cql_train.id2cql)